## Spatial Data Science with CityJSON

The purpose of this Notebook is to ***work with*** the product of [osm_LoD1_3DCityModel](https://github.com/AdrianKriger/osm_LoD1_3DCityModel); a previously created CityJSON city model.

<div class="alert alert-block alert-warning"><b>This notebook will:</b>

> **1. allow the user to execute an application of Spatial Data Science**  
>
>> **a)  [population estimation](#Section1a)** _--with a previous census metric population growth rate and projected (future) population are also possible_  **and**  
>> **b)  a measure of [Building Volume per Capita](#Section1b)**
>
> **2. further applications of Spatial Data Science**  
>
>> -  calculate percentage **homes and population with direct access to on-site renewable energy infrastructure** *--rooftop photovoltaic panels (PV) and solar water heaters (SWH).*
>
> **3. produce [an interactive visualization](#Section1b)** *-via [pydeck](https://deckgl.readthedocs.io/en/latest/)- which a user can navigate, query and share* **that**;
> > **a) [colour buildings by type](#Section2a)** *(to easily visualize building stock)* 
>
> **4. propose several [Geography and Sustainable Development Education *conversation starters*](#Section3) for Secondary and Tertiary level students**
</div>

<div class="alert alert-block alert-danger"><b>Please Note:</b>

***The [village](https://github.com/AdrianKriger/geo3D/tree/main/village)*** processing option is meant for areas with no more than for **2 500 buildings**.</div>

In [1]:
#- load the magic

%matplotlib inline
import os
from pathlib import Path

import numpy as np
import pandas as pd
import shapely
from shapely.geometry import Polygon, shape, mapping
import json
import geojson

import city3D as city3D

from cjio import cityjson

import matplotlib.pyplot as plt
import pydeck as pdk

In [2]:
import warnings
warnings.filterwarnings('ignore')

**The area under investigation is [Mamre, Cape Town. South Africa](https://en.wikipedia.org/wiki/Mamre,_South_Africa).**

In [3]:
#- change to harvest the appropriate CityJSON

#jparams = json.load(open('uEstate_param.json'))
#jparams = json.load(open('cput_param.json'))
#jparams = json.load(open('saao_param.json'))
jparams = json.load(open('mamre_param.json'))
#jparams = json.load(open('sRiver_param.json'))

In [4]:
cm = cityjson.load(path=jparams['cjsn_solid']) #-- citjsnClean_rural3D.json in the result folder

In [5]:
print(cm)

CityJSON version = 1.1
EPSG = 32734
bbox = [263859.53151571925, 6287898.265465543, 145.1199951171875, 266646.4893499555, 6290185.027937451, 254.5399932861328]
=== CityObjects ===
|-- TINRelief (1)
|-- Building (2316)
materials = False
textures = False


In [6]:
df = cm.to_dataframe()
#- remove the first feature: the terrain
df = df[1:]    

#- harvest the crs
theinfo = cm.get_info()
crs = theinfo[1]

# account for holes
def coords_to_polygon(rings):
    outer = rings[0]                              # first ring is the shell
    holes = rings[1:] if len(rings) > 1 else None
    return Polygon(shell=outer, holes=holes)

# Convert JSON string to Python list
df['footprint_coords_list'] = df['footprint'].apply(json.loads)

# create home-baked gdf
#gdf = gpd.GeoDataFrame(df, geometry=df['footprint_coords_list'].apply(coords_to_polygon), crs=crs[7:])#jparams['crs'])
gdf = city3D.GeoDataFrameLite(df)
gdf['geometry'] = gdf['footprint_coords_list'].apply(coords_to_polygon)
gdf.crs = crs[7:]
# Drop columns inplace
gdf.drop(columns=['footprint', 'footprint_coords_list'], inplace=True)
#gdf.head(2)

## 1. Spatial Data Science

<div class="alert alert-block alert-warning"><b>We start with basic spatial analysis</b>  
    
     
- We'll [estimate the population](#Section1a), within our area of interest, and then  
- calculate the [Building Volume Per Capita (BVPC)](#Section1b).
</div>

While estimating population is well documented; recent investigations to **understand overcrowding** have led to newer measurements.  

The most noteable of these is **Building Volume Per Capita (BVPC)** [(Ghosh, T; et al. 2020)](https://www.researchgate.net/publication/343185735_Building_Volume_Per_Capita_BVPC_A_Spatially_Explicit_Measure_of_Inequality_Relevant_to_the_SDGs). BVPC is the cubic meters of building per person. **BVPC tells us how much space one person has per residential living unit** (a house / apartment / etc.). It is ***a proxy measure of economic inequality and a direct measure of housing inequality***.

BVPC builds on the work of [(Reddy, A and Leslie, T.F., 2013)](https://www.tandfonline.com/doi/abs/10.1080/02723638.2015.1060696?journalCode=rurb20) and attempts to integrate with several **[Sustainable Development Goals](https://sdgs.un.org/goals)** (most noteably: **[SDG 11: Developing sustainable cities and communities](https://sdgs.un.org/goals/goal11)**) and captures the average ***'living space'*** each person has in their home.

<div class="alert alert-block alert-info"><b>These analysis expect the user to have some basic knowledge about the environment under inquiry / investigation</b> </div>

In [7]:
gdf.head(2)

id       osm_id building building:levels  building_height  \
328118446  0  328118446.0      yes               1              4.1   
328118447  1  328118447.0   church               2              6.9   

           roof_height  ground_height     plus_code  \
328118446       183.53     179.429993  4FRWFFVC+P79   
328118447       185.94     179.039993  4FRWFFVC+H9Q   

                                                     address  \
328118446                                                NaN   
328118447  Moravian Church South Africa Kerk Street Mamre...   

                    amenity operator residential  bottom_roof_height  \
328118446               NaN      NaN         NaN                 NaN   
328118447  place_of_worship      NaN         NaN                 NaN   

          building:use                                           geometry  
328118446          NaN  POLYGON ((265041.6351569728 6289775.0592048075...  
328118447          NaN  POLYGON ((265070.9766813367 6289761.325392997,...

In [8]:
#gdf.plot()
# have a look at the building type and amenities available
gdf['building'].unique()

array(['yes', 'church', 'house', 'cabin', 'public', 'civic', 'office',
       'retail', 'clinic', 'school', 'garage', 'greenhouse', 'roof',
       'kindergarten', 'clubhouse', 'guest_house', 'service', 'detached',
       'shed'], dtype=object)

<a id='Section1a'></a>

<div class="alert alert-block alert-success"><b>1.  a) Estimate Population:</b> 
    
_(with population growth rate and population projection possible too)_ </div>

In [9]:
#--we only want building=house or =apartment or =residential
gdf2 = gdf[gdf["building"].isin(['house', 'semidetached_house', 'terrace', 'terraced', 'apartments', 'residential', 'dormitory', 'cabin'])].copy()

In [10]:
#- some data wrangling to replace 'bld:residential' to 'bld:student' if 'residential:student'
gdf_pop = gdf2.copy()

if 'residential' in gdf_pop.columns:
    df_res = gdf_pop[gdf_pop['residential'] == 'student']
    #df_res = df2[df2['building:use'] != None]
    df_res = df_res[~df_res['residential'].isna()]
    gdf_pop.loc[df_res.index, 'building'] = df_res['residential'] 

#- some more data wrangling
with pd.option_context("future.no_silent_downcasting", True):
    if 'building:flats' in gdf_pop.columns: 
        gdf_pop['building:flats'] = pd.to_numeric(gdf_pop['building:flats'].fillna(0).infer_objects(copy=False))
    if 'building:units' in gdf_pop.columns:    
        gdf_pop['building:units'] = pd.to_numeric(gdf_pop['building:units'].fillna(0).infer_objects(copy=False))
    if 'beds' in gdf_pop.columns:   
        gdf_pop['beds'] = pd.to_numeric(gdf_pop['beds'].fillna(0).infer_objects(copy=False))
    if 'rooms' in gdf_pop.columns:   
        gdf_pop['rooms'] = pd.to_numeric(gdf_pop['rooms'].fillna(0).infer_objects(copy=False))

gdf_pop["building:levels"] = pd.to_numeric(gdf_pop["building:levels"])

gdf_pop.head(2)

id       osm_id building  building:levels  building_height  \
656840974  7  656840974.0    house                1              4.1   
656840975  8  656840975.0    house                1              4.1   

           roof_height  ground_height     plus_code  \
656840974       174.78     170.679993  4FRWFFM9+X98   
656840975       174.78     170.679993  4FRWFFM9+X9X   

                                     address amenity operator residential  \
656840974  39 Dove Lane Mamre 7347 Cape Town     NaN      NaN         NaN   
656840975  37 Dove Lane Mamre 7347 Cape Town     NaN      NaN         NaN   

           bottom_roof_height building:use  \
656840974                 NaN          NaN   
656840975                 NaN          NaN   

                                                    geometry  
656840974  POLYGON ((264864.98193212313 6288741.008398377...  
656840975  POLYGON ((264865.3504529182 6288749.140981195,...

In [11]:
gdf_pop['building'].value_counts()

building
house    1643
cabin     376
Name: count, dtype: int64

**This area** (Mamre) **is peri-urban with single level housing units. To estimate population is thus pretty straight forward.**

<div class="alert alert-block alert-info"><b>We start with local knowledge.</b></div>

**On average there are roughly `6` people per `building:house` in this area.**  

An ***informal*** structure ([shack](https://en.wikipedia.org/wiki/Shack)) is tagged [building:cabin](https://wiki.openstreetmap.org/wiki/Tag:building%3Dcabin) and houses `4` people.

<div class="alert alert-block alert-danger"><b>Your Participation! </b>
    

We will execute the calculation programmatically. **Fill in the relevant variables in the _`cell`_ below** </div>

In [12]:
#- average number of residents per formal house
f_house = 6
#- average number of residents per informal structure
inf_structure = 4

<div class="alert alert-block alert-warning"><b></b>  
    
**Furthermore:**  
    - **[social housing](https://en.wikipedia.org/wiki/Public_housing)** is tagged `building:residential` with the number of occupants iether *the number of informal structure occupants* or `building:flats * inf_structure`  
    - A `social_facility` (carehome, shelter, etc.) harvests the `beds` *'key:value'* pair.  
    - `building:apartment` harvests the `building:flats` *'key:value'* pair *(the number of units)* to calculate `*3` people per apartment.  
    - ***Student accomodation***:  
>    - University owed: is tagged `building:dormitory` with `residential:university` and harvests the `beds` *'key:value'* pair.
>    - Private for-profit: is tagged `building:residential` or `:dormitory` with `residential:student` and then harvests the `building:flats` or `:rooms` *'key:value'* pair *(the number of units)* to calculate `*1` people per apartment; if `level: > 1` else `*3` people in a house share.
    
**The tagging scheme and numbers is based on *how your community is mapped* and local knowledge**
</div>

In [13]:
c = gdf_pop.columns

def pop(row):
    #- formal house
    if row['building'] == 'house' or row['building'] == 'semidetached_house':
        return f_house
    if row['building'] == 'terrace' and 'building:units' in c or row['building'] == 'terraced' and 'building:units' in c:
        return row['building:units'] * f_house

    #- informal structure (shack)
    if row['building'] == 'cabin':
        return inf_structure

    #- in this case social housing
    if row['building'] == 'residential' and 'social_facility' in c and row['social_facility'] is np.nan:
        if row['building:levels'] > 1:
            if 'rooms' in c and row['rooms'] != 0:
                return row['rooms']
            if 'building:flats' in c and row['building:flats'] != 0:
                return row['building:flats'] * inf_structure
        else:
            return inf_structure

    #-- social facility [shelter / carehome]
    if row['building'] == 'residential' and 'social_facility' in c and row['social_facility'] is not np.nan:
        if row['building:levels'] > 1:
            if 'building:units' in c and row['building:units'] != 0:
                return row['building:units'] 
            if 'beds' in c and row['beds'] != 0:
                return row['beds']
        else:
            return inf_structure

    #- formal apartment
    if row['building'] == 'apartments':
        if 'rooms' in c and row['rooms'] != 0:
            return row['rooms']
        else:
            return row['building:flats'] * 3
        
    #- private student residence 
    if row['building'] == 'student':
        if row['building:levels'] > 1:
            if 'rooms' in c and row['rooms'] != 0:
                return row['rooms']
            else:
                return row['building:flats']
        else:
            return 3
            
    # university owned student residence
    if row['building'] == 'dormitory' and row['residential'] == 'university':
        if row['building:levels'] > 1:
            if 'rooms' in c and row['rooms'] != 0:
                return row['rooms']
            if 'beds' in c and row['beds'] != 0:
                return row['beds']
        else:
            return 3

gdf_pop['pop'] = gdf_pop.apply(lambda x: pop(x), axis=1)

est_pop = gdf_pop['pop'].sum()
print('The estimated population is:', est_pop)

The estimated population is: 11362


**The official [STATSSA 2011 census figure](https://www.statssa.gov.za/?page_id=4286&id=291), for this community, is 9048.**

We can calculate the annual population growth rate using the formula for **[Annual population growth](https://databank.worldbank.org/metadataglossary/health-nutrition-and-population-statistics/series/SP.POP.GROW):**

$$r = \frac{\ln{[\frac{End Population}{Start Population}}]}{n} * 100 = \frac{\ln{[\frac{11 120^{*}}{9048}}]}{12} * 100   = 1.43\%$$
<br>
<sup>* <sub>***Notice!*** The estimated population (11176) is **NOT** the number in the formula (11 120). This community is frequently updated on OpenStreetMap and variations are common.</sub> 

<div class="alert alert-block alert-danger"><b>Your Participation! </b>
    

It is possible to execute the calculation programmatically. **Fill in the relevant variables in the _`cell`_ below** </div>

In [14]:
#- previous population
start_population = 9048                                #- uEstate estimate: 987 

#- period in years from the previous census
years = 12

In [15]:
#-execute
r = (np.log(est_pop/start_population)/years) * 100
print('population growth rate of approximately:', round(r, 2), '%')

population growth rate of approximately: 1.9 %


To conclude; we can project into the future with a very basic formula to estimate the population _x_-years from now:  

$$p  = P_o * (1 + r)^{t} = p = 10736 * (1 + 0.0143)^{10}  = 12 368$$

<div class="alert alert-block alert-danger"><b>Your Participation! </b>
    

It is possible to execute the calculation programmatically. **Fill in the variables in the _`cell`_ below** </div>

In [16]:
#- period in years from now
years = 10

In [17]:
#p = est_pop * (1 + (r/100))**years

#print('estimated population', years ,'years from now:', int(p))

#- account for non-residential areas without failure
#- helper function
def safe_population_estimate(est_pop, r, years):
    try:
        p = est_pop * (1 + (r / 100))**years
        return int(p)
    except Exception as e:
        print(f"Population estimate failed: {e}")
        return None  # keeps notebook running

#- execute function
p = safe_population_estimate(est_pop, r, years)

#- shows error and moves on
if p is not None:
    print(f"estimated population {years} years from now: {p}")

estimated population 10 years from now: 13712


<a id='Section1b'></a>

<div class="alert alert-block alert-success"><b>1. b) Building Volume Per Capita (BVPC):</b>  
BVPC = total population of a community divided by sum of building volume</div>

In [18]:
#gdf_pop.head(3)

In [19]:
#gdf_pop['area'] = gdf_pop['geometry'].area#\.map(lambda p: p.area)
gdf_pop['area'] = gdf_pop['geometry'].apply(lambda geom: geom.area if geom else 0)
gdf_pop['volume'] = gdf_pop['area'] * gdf_pop['building_height']

#- remove the volume of the ground floor (unoccupied) when building:levels > 7 [this is an arbitrary number based on local knowledge]
#- typically the space is reserved for some other function: retail, etc. 
gdf_pop['volume'] = [
    (row['volume'] - row['area'] * 2.8) if (
        'social_facility' in row and row['social_facility'] is np.nan and row['building:levels'] > 7 and
        row['building'] in ['residential', 'apartments', 'student']
    ) else row['volume']
    for _, row in gdf_pop.iterrows()
]

gdf_pop['bvpc'] =  gdf_pop['volume'] / gdf_pop['pop']

gdf_pop.tail(2)

id      osm_id building  building:levels  building_height  \
12289266  2341  12289266.0    house                1              4.1   
12357148  2342  12357148.0    house                1              4.1   

          roof_height  ground_height     plus_code  \
12289266       189.86     185.759995  4FRWFFMF+W7J   
12357148       197.36     193.259995  4FRWFFPJ+P7W   

                                           address amenity operator  \
12289266  22 Clarkeson Street Mamre 7347 Cape Town     NaN      NaN   
12357148         2 Tol Street Mamre 7347 Cape Town     NaN      NaN   

         residential  bottom_roof_height building:use  \
12289266         NaN                 NaN          NaN   
12357148         NaN                 NaN          NaN   

                                                   geometry  pop        area  \
12289266  POLYGON ((265302.8715881496 6288753.930217357,...    6  344.679759   
12357148  POLYGON ((265989.6485932828 6288995.734908563,...    6  329.189435   

               volume        bvpc  
12289266  1413.187012  235.531169  
12357148  1349.676685  224.946114

In [20]:
print(gdf_pop['bvpc'].describe())

count    2019.000000
mean       75.260050
std        50.350782
min         7.419412
25%        33.119812
50%        65.729917
75%       101.878902
max       400.313316
Name: bvpc, dtype: float64


In [21]:
bvpc = round(gdf_pop['volume'].sum() / est_pop, 3)

print('Building Volume Per Capita (BVPC):', bvpc)

Building Volume Per Capita (BVPC): 77.819


<div class="alert alert-block alert-info"><b></b>

**This BVPC value is general.**  

We can seperate `building:house` from `building:cabin` and `building:residential` to undertand the differences between ***formal and informal*** housing in this area.
    
**We want to understand the living space *(the cubic-meter BVPC value)* each person has in thier home**
</div>

In [22]:
formal = gdf_pop[gdf_pop["building"].isin(['house', 'semidetached_house', 'terrace', 'terraced', 'apartments'])].copy()
f_pop = formal['pop'].sum()
#f_area = formal['area'].mean()

informal = gdf_pop[gdf_pop["building"].isin(['residential', 'cabin'])].copy()
inf_pop = informal['pop'].sum()
#inf_area = formal['area'].mean()

#- student
stu = gdf_pop[gdf_pop["building"].isin(['student', 'dormitory'])].copy()
stu_pop = stu['pop'].sum()

bvpc_formal = round(formal['volume'].sum() / formal['pop'].sum()if formal['pop'].sum() != 0 else 0, 3)
bvpc_informal = round(informal['volume'].sum() / informal['pop'].sum() if informal['pop'].sum() != 0 else 0, 3)
bvpc_stu = round(stu['volume'].sum() / stu['pop'].sum() if stu['pop'].sum() != 0 else 0, 3)

print('FORMAL: Population: ', f_pop, ' with Building Volume Per Capita (BVPC):', bvpc_formal)
print('')
print('STUDENT RESIDENCE: Population: ', stu_pop, ' with Building Volume Per Capita (BVPC):', bvpc_stu)
print('')
print('INFORMAL: Population: ', inf_pop, ' with Building Volume Per Capita (BVPC)', bvpc_informal)

FORMAL: Population:  9858  with Building Volume Per Capita (BVPC): 84.108

STUDENT RESIDENCE: Population:  0  with Building Volume Per Capita (BVPC): 0

INFORMAL: Population:  1504  with Building Volume Per Capita (BVPC) 36.596


<div class="alert alert-block alert-danger"><b>Warning: </b>
    

These are LoD1 3D City Models and works well in these types of areas.  
LoD2 would offer a more representative BVpC [(Ghosh, T; et al. 2020)](https://www.researchgate.net/publication/343185735_Building_Volume_Per_Capita_BVPC_A_Spatially_Explicit_Measure_of_Inequality_Relevant_to_the_SDGs) value; when the complexity of the built environment increases.  

Think about a `house` with living space in the roof structure, so called *'attic living'*, or an `apartment` / `residential` building with different levels, loft apartments and/or units in the turrets of a `building`. 

***consider***: this area seperates [building:cabin](https://wiki.openstreetmap.org/wiki/Tag:building%3Dcabin) from `building:residential` to more precisely represent informal structures without typical roof trussess but account for [social housing](https://en.wikipedia.org/wiki/Public_housing) that does</div>

## 2. Further examples of Spatial Data Science *(renewable energy)*:

<div class="alert alert-block alert-warning"><b></b>

**Let's attempt to understand the % of homes and population served with renewable energy.**
</div>
    
[**SDG**](https://sdgs.un.org/goals) indicators are typically calculated at **region and national scales**.  
Here, because we are working with highly detailed, local data, we can explore what a [**Tier 3 local indicator**](https://unstats.un.org/sdgs/metadata/) might look like at a ***neighbourhood level***.
<br>

In this section 3. we evaluate [**SDG 7: Ensure access to affordable, reliable, sustainable and modern energy for all**](https://sdgs.un.org/goals/goal7) at a community level and estimate the **proportion of residential units and population** that have **direct access to on-site renewable energy infrastructure** *--rooftop photovoltaic panels (PV) and solar water heaters (SWH)*.

- Percentage of **households** served by rooftop renewable energy  
- Percentage of the **population** served by rooftop renewable energy

</div>

In [23]:
#- harvest rooftop solar

query = """
     [out:json][timeout:30];
    // --when areas have duplicate names given the world has a limited amount of uniquely named places
    area[name='{0}'] ->.b;
    // -- target area ~ can be way or relation
    wr(area.b)[name='{1}'];
    map_to_area -> .a;
    (
        way["power"="generator"]["generator:source"="solar"](area.a);                // Catches simple generators
       //  way["power"="solar_photovoltaic_panel"](area.a);                          // Catches the alternate tag
    );
    out geom;
    """.format(jparams['LargeArea'], jparams['FocusArea'])

#- execute function from city3D, harvest generator solar and return GeoDataFrameLite | home-baked gdf
sol = city3D.overpass_to_gdf(query)
#sol = sol.to_crs(epsg)
sol = sol.to_crs(crs[7:])


if len(sol) < 0:
    print("\033[0m No rooftop solar are mapped in", jparams['FocusArea'])

In [24]:
#- look
sol.head(2)

generator:method generator:output:hot_water generator:source  \
0          thermal                        yes            solar   
1          thermal                        yes            solar   

            generator:type location      power start_date area  \
0  solar_thermal_collector     roof  generator        NaN  NaN   
1  solar_thermal_collector     roof  generator        NaN  NaN   

                                            geometry      osm_id osm_type  
0  POLYGON ((266074.7976815852 6288576.002370844,...  1095737675      way  
1  POLYGON ((266194.47713799647 6288764.539267579...  1095739760      way

In [25]:
#- the number of renewable in AREA
sol['generator:method'].value_counts()

generator:method
thermal    50
Name: count, dtype: int64

In [26]:
# join (link) rooftop renewable energy to the appropriate bld
def buildings_with_solar(gdf_buildings, gdf_solar):
    # Prepare output arrays
    solar_ids_per_building = [[] for _ in range(len(gdf_buildings["geometry"]))]
    solar_types_per_building = [[] for _ in range(len(gdf_buildings))]
    
    for i, b_geom in enumerate(gdf_buildings["geometry"]):
        for j, s_geom in enumerate(gdf_solar["geometry"]):
            #if b_geom.intersects(s_geom):
            if b_geom.contains(s_geom):
                solar_ids_per_building[i].append(gdf_solar["osm_id"].iloc[j])
                solar_types_per_building[i].append(gdf_solar["generator:method"].iloc[j])

    #- keep only unique values
    #unique_methods_per_building = [list(set(lst)) for lst in solar_types_per_building]
    
    gdf_buildings["solar_ids"] = solar_ids_per_building
    gdf_buildings["generator:method"] = solar_types_per_building #unique_methods_per_building
    gdf_buildings["has_solar"] = [len(lst) > 0 for lst in solar_ids_per_building]
    gdf_buildings["solar_ids"] = solar_ids_per_building
    
    return gdf_buildings

blds = buildings_with_solar(gdf_pop, sol)
blds.head(2)

id       osm_id building  building:levels  building_height  \
656840974  7  656840974.0    house                1              4.1   
656840975  8  656840975.0    house                1              4.1   

           roof_height  ground_height     plus_code  \
656840974       174.78     170.679993  4FRWFFM9+X98   
656840975       174.78     170.679993  4FRWFFM9+X9X   

                                     address amenity  ... bottom_roof_height  \
656840974  39 Dove Lane Mamre 7347 Cape Town     NaN  ...                NaN   
656840975  37 Dove Lane Mamre 7347 Cape Town     NaN  ...                NaN   

          building:use                                           geometry pop  \
656840974          NaN  POLYGON ((264864.98193212313 6288741.008398377...   6   
656840975          NaN  POLYGON ((264865.3504529182 6288749.140981195,...   6   

                area      volume       bvpc     solar_ids  generator:method  \
656840974  38.658416  158.499506  26.416584            []                []   
656840975  39.833421  163.317028  27.219505  [1096772168]         [thermal]   

          has_solar  
656840974     False  
656840975      True  

[2 rows x 22 columns]

<div class="alert alert-block alert-success"><b>Percentage of households served by rooftop renewable energy</b></div>

$$ \text{\% homes with renewable energy} = \frac{\text{Number of dwellings with mapped solar PV or SWH}}{\text{Total number of dwellings}} \times 100 $$

In [27]:
#- harvest columns
with_solar = sum(blds["has_solar"])
pop = est_pop #gdf["pop"]
total_homes = len(blds)

solHms = round(with_solar / total_homes * 100, 2)

print('\033[1m Percentage homes, \033[0m in', jparams['FocusArea'],', with rooftop photovoltaic panels (PV) and solar water heaters (SWH):', solHms)

 Percentage homes,  in Mamre , with rooftop photovoltaic panels (PV) and solar water heaters (SWH): 2.38


<div class="alert alert-block alert-success"><b>Percentage of population served by rooftop renewable energy</b></div>

$$ \text{\% population with renewable energy} = \frac{\text{Number of residents with mapped solar PV and SWH}}{\text{Estimated population}} \times 100 $$

In [28]:
#pop_total = gdf_pop["pop"].sum()
pop_total = blds["pop"].sum()
#pop_solar = gdf_pop["pop"][blds["has_solar"]].sum()
pop_solar = blds["pop"][blds["has_solar"]].sum()


solPop = round(pop_solar / pop_total * 100, 2)

print('\033[1m Percentage population, \033[0m in', jparams['FocusArea'],', with rooftop photovoltaic panels (PV) and solar water heaters (SWH):', solPop)

 Percentage population,  in Mamre , with rooftop photovoltaic panels (PV) and solar water heaters (SWH): 2.53


In [29]:
# number of solar renewable on HOMES
blds['generator:method'].explode().value_counts()

generator:method
thermal    48
Name: count, dtype: int64

## 3. Interactive Visualization

You might want to create and share an `html` visualization.

<div class="alert alert-block alert-warning"><b> </b>  
    
_In this example we identify building stock by **color** but you are limited only through your imagination and the data you have access too_
</div>

In [30]:
gdf.crs

<Projected CRS: EPSG:32734>
Name: WGS 84 / UTM zone 34S
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 18°E and 24°E, southern hemisphere between 80°S and equator, onshore and offshore. Angola. Botswana. Democratic Republic of the Congo (Zaire). Namibia. South Africa. Zambia.
- bounds: (18.0, -80.0, 24.0, 0.0)
Coordinate Operation:
- name: UTM zone 34S
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

<img src="data/proj.png" alt="proj" width="550" align="right"/>
<br>
<br>

We need a ***Geographic*** Coordinate Reference System.

        <Geographic 2D CRS: EPSG:4326>
        Name: WGS 84
        Axis Info [ellipsoidal]:
        - Lat[north]: Geodetic latitude (degree)
        - Lon[east]: Geodetic longitude (degree)
        Area of Use:
        - name: World.
        - bounds: (-180.0, -90.0, 180.0, 90.0)
        Datum: World Geodetic System 1984 ensemble
        - Ellipsoid: WGS 84
        - Prime Meridian: Greenwich

In [31]:
#- pydeck needs geographic coords
gdf = gdf.to_crs(4326)

In [32]:
# -- get the location for pydeck

# combine all geometries
geom = shapely.unary_union(gdf['geometry'])
# centroid
xy = (geom.centroid.x, geom.centroid.y)

# bounding box
minx, miny, maxx, maxy = geom.bounds
bbox = [minx, miny, maxx, maxy]

In [33]:
# have a look at the building type and amenities available
gdf['building'].unique()

array(['yes', 'church', 'house', 'cabin', 'public', 'civic', 'office',
       'retail', 'clinic', 'school', 'garage', 'greenhouse', 'roof',
       'kindergarten', 'clubhouse', 'guest_house', 'service', 'detached',
       'shed'], dtype=object)

<a id='Section2a'></a>
<div class="alert alert-block alert-success"><b>Building Stock:</b> To differentiate a school, housing, retail, healthcare and community focused facilities (library, municipal office, community centre) we color the buildings - we harvest the osm tags [amenity and building type] directly.</div>

In [34]:
# colour buildings based on use / amenity
def color(bld):
    #- formal house
    if bld == 'house' or bld == 'semidetached_house' or bld == 'terrace': #- add maisonette, duplex, etc. 
        return [255, 255, 204]                        #-grey
    if bld == 'apartments':
        return [252, 194, 3]                          #-orange 
    #- informal structure / social housing / student
    if bld == 'residential' or bld == 'dormitory' or bld == 'student' or bld == 'cabin':
        return [119, 3, 252]                          #-purple
        
    if bld == 'garage' or bld == 'parking':
        return [3, 132, 252]                          #-blue        
    if bld == 'retail' or bld == 'supermarket':
        return [253, 141, 60]
    if bld == 'office' or bld == 'commercial':
        return [185, 206, 37]
    if bld == 'school' or bld == 'kindergarten' or bld == 'university' or bld == 'college':
        return [128, 0, 38]
    if bld == 'clinic' or bld == 'doctors' or bld == 'hospital':
        return [89, 182, 178]
    if bld == 'community_centre' or bld == 'service' or bld == 'post_office' or bld == 'hall' \
    or bld ==  'townhall' or bld == 'police' or bld == 'library' or bld == 'fire_station' :
        return [181, 182, 89]
    if bld == 'warehouse' or bld == 'industrial':
        return [193, 255, 193]
    if bld == 'hotel':
        return [139, 117, 0]
    if bld == 'church' or bld == 'mosque' or bld == 'synagogue':
        return [225, 225, 51]
    else:
        return [255, 255, 204]

gdf["fill_color"] = gdf['building'].apply(lambda x: color(x))

In [35]:
#- look
gdf.head(2)

id       osm_id building building:levels  building_height  \
328118446  0  328118446.0      yes               1              4.1   
328118447  1  328118447.0   church               2              6.9   

           roof_height  ground_height     plus_code  \
328118446       183.53     179.429993  4FRWFFVC+P79   
328118447       185.94     179.039993  4FRWFFVC+H9Q   

                                                     address  \
328118446                                                NaN   
328118447  Moravian Church South Africa Kerk Street Mamre...   

                    amenity operator residential  bottom_roof_height  \
328118446               NaN      NaN         NaN                 NaN   
328118447  place_of_worship      NaN         NaN                 NaN   

          building:use                                           geometry  \
328118446          NaN  POLYGON ((18.4706033 -33.505787600000005, 18.4...   
328118447          NaN  POLYGON ((18.4709153 -33.5059178, 18.4709287 -...   

                fill_color  
328118446  [255, 255, 204]  
328118447   [225, 225, 51]

In [36]:
## ~ (x, y) - bl, tl, tr, br  ~~ or ~~ sw, nw, ne, se
#area = [[[18.4377, -33.9307], [18.4377, -33.9283], [18.4418, -33.9283], [18.4418, -33.9307]]]
area = [[[bbox[0], bbox[1]], [bbox[0], bbox[3]], 
         [bbox[2], bbox[3]], [bbox[2], bbox[1]]]]

builds = city3D.gdf_to_geojson(gdf)

## ~ (y, x)
view_state = pdk.ViewState(latitude=xy[1], longitude=xy[0], zoom=16.5, max_zoom=19, pitch=72, 
                                   bearing=80)

land = pdk.Layer(
    "PolygonLayer",
    area,
    stroked=False,
    # processes the data as a flat longitude-latitude pair
    get_polygon="-",
    get_fill_color=[0, 0, 0, 1],
    #material = True,
    #shadowEnabled = True
)
building_layer = pdk.Layer(
    #"PolygonLayer",
    "GeoJsonLayer",
    builds,
    opacity=0.3,
    stroked=False,
    get_polygon="geometry.coordinates",
    filled=True,
    extruded=True,
    wireframe=False,
    get_elevation="properties.building_height",
    get_fill_color="properties.fill_color",
    get_line_color="properties.fill_color",
    #material = True, 
    #shadowEnabled = True, 
    auto_highlight=True,
    pickable=True,
)

tooltip = {"html": "<b>Levels:</b> {building:levels} <br/> <b>Address:</b> {address}\
<br/> <b>Plus Code:</b> {plus_code} <br/> <b>Building Type:</b> {building}"}

#change the tooltip to show bus routes and comment out the previous
#tooltip = {"html": "<b>Route:</b> {name} <br/>"}

r = pdk.Deck(layers=[land,  building_layer],#, greenspaces_layer, p_layer, water_layer, r_layer], #
             #views=[{"@@type": "MapView", "controller": True}],
             initial_view_state=view_state,
             map_style = 'dark_no_labels', #pdk.map_styles.LIGHT,
             tooltip=tooltip)
#save
r.to_html("./result/interactiveAlt.html", offline=True)

**on a laptop without a mouse:**

- `trackpad left-click drag-left` and `-right`;
- `Ctrl left-click drag-up`, `-down`, `-left` and `-right` to rotate and so-on and
- `+` next to Backspace zoom-in and `-` next to `+` zoom-out.

**Now you do your community.** ~ If your area needs [OpenStreetMap](https://en.wikipedia.org/wiki/OpenStreetMap)  data and you want to contribute please follow the [Guide](https://wiki.openstreetmap.org/wiki/Beginners%27_guide).

<a id='Section3'></a>

<div class="alert alert-block alert-warning"><b>  </b>  
    
**To understand the performance in an [Urban setting](https://en.wikipedia.org/wiki/Urban_area) change `cell [2]` above:**

<span style="color:black">**jparams**</span> = <span style="color:Darkred">uEstate</span> <span style="color:black">(['University Estate'](https://en.wikipedia.org/wiki/University_Estate)) or</span> <span style="color:Darkred">sRiver</span>  <span style="color:black">(['Salt River'](https://en.wikipedia.org/wiki/Salt_River,_Cape_Town)) or</span> <span style="color:Darkred">obs</span> <span style="color:black">(['Observatory'](https://en.wikipedia.org/wiki/Observatory,_Cape_Town)) *(with residents per formal house = 4 | 5 in Salt River and residents per informal structure = 3)*</span> <span style="color:black">and</span>  <span style="color:Darkred">cput</span> <span style="color:black">('Cape Peninsula University of Technology (Bellville Campus)')</span>       
</div>

## 4. Possible Secondary and Tertiary level *conversations starters*:

<div class="alert alert-block alert-success"><b>communicate and exchange ideas and understanding</b></div>

| **Topic**                                | **Secondary Level Questions**                                                                                                                                                                                   | **Tertiary Level Questions**                                                                                                                                                                                                                   |
|------------------------------------------|-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| **Basic Understanding and Observations** | - What types of buildings are most common in the area (houses, apartments, retail, etc.)?<br>- Can you identify any patterns in the distribution of different types of buildings (e.g., are retail stores concentrated in certain areas)? | - How does the building stock composition (e.g., ratio of houses) correlate with the population? *demographics (e.g., age distribution, household size) for the area will strengthen the analysis!* <br>- Analyze the relationship between building density and population. What urban planning theories can explain this relationship? |
| **Spatial Relationships and Impacts**    | - How does the location of residential areas compare to the location of retail and commercial areas?<br>- What impact might the density and distribution of buildings have on local traffic and transportation?<br>- How might the population distribution affect the demand for local services such as schools, hospitals, and parks? | - Evaluate the accessibility of essential services (e.g., healthcare, education) in relation to the population and building types.<br>- Assess the potential social and economic impacts of a proposed new residential or commercial development in the area.                  |
| **Socioeconomic and Environmental Considerations** | - Are there any correlations between the types of housing available and the household size? *additional demographics (e.g., income level) for the area will strengthen the analysis!*<br>- How might the current building stock and population influence the local economy? *demographics (e.g., age distribution, household size) for the area will strengthen the analysis!*<br>- What are some potential environmental impacts of the current building distribution, such as green space availability or pollution levels? | - How does the current building stock support or hinder sustainable development goals (e.g., energy efficiency, reduced carbon footprint)?<br>- What strategies could be implemented to increase the resilience of the community to environmental or economic changes?                       |
| **Future Planning and Development**      | - Based on the current building stock and population metrics, what areas might benefit from additional housing or commercial development?<br>- How could urban planners use this information to improve the quality of life in the area?<br>- What changes would you recommend to better balance residential, commercial, and recreational spaces? | - How might different zoning regulations impact the distribution of residential, commercial, and industrial buildings in the future?<br>- Propose urban design solutions that could improve the sustainability and livability of the area, considering both current metrics and future projections. |
| **Quantitative and Qualitative Research** | |- Design a research study to investigate the impact of building type diversity on community wellbeing. What methodologies would you use?<br>- Analyze historical data to understand trends in building development and population growth. How have these trends shaped the current urban landscape?<br>- Conduct a SWOT analysis (Strengths, Weaknesses, Opportunities, Threats) of the area based on the building stock and population metrics. |

***

**Now you do your community.** ~ If your area needs [OpenStreetMap](https://en.wikipedia.org/wiki/OpenStreetMap) data and you want to contribute please follow the [Guide](https://wiki.openstreetmap.org/wiki/Beginners%27_guide). 